In [1]:
import utilities as util
import difflib
from scipy import spatial
from scipy import array
from scipy.stats import mode
import time
import numpy as np
import reedsolo
from collections import OrderedDict

Data from Bas' file

In [158]:
dropletlist = []
with open("sequenced.txt", 'r') as f:
    for line in f:
        if len(line) == 153:
            dropletlist.append(line.rstrip('\n'))

In [159]:
len(dropletlist)

134816

Erlich et al. mention that they only collapse identical sequences. So I will attempt to do that here.


In [160]:
def collapse(sim_results):
    sequences =  {}
    for i in sim_results:
        i = int(util.DNA2Binary(i),2)
        if i not in sequences:
            sequences[i] = 1 
        else: 
            sequences[i] += 1
    return sequences

In [161]:
collapsed = collapse(dropletlist)

In [5]:
def HammingDistance(num1,num2):
    return bin(num1 ^ num2).count("1")

In [6]:
groups={}
ungrouped = []
for i in collapsed:
    if collapsed[i] > 1: 
        groups[i] = collapsed[i]
    else:
        ungrouped.append(i)

{0: ['1', '1', '1', '1'], 1: ['1', '1', '1', '1'], 2: ['1', '1', '1', '1'], 3: ['0', '1', '1', '1'], 4: ['1', '1', '1', '1'], 5: ['1', '1', '1', '1'], 6: ['1', '0', '0', '0'], 7: ['1', '0', '0', '0'], 8: ['0', '1', '1', '1'], 9: ['0', '1', '1', '1'], 10: ['1', '1', '1', '1'], 11: ['1', '0', '0', '0'], 12: ['1', '1', '1', '1'], 13: ['0', '0', '0', '0'], 14: ['1', '0', '0', '0'], 15: ['0', '1', '1', '1'], 16: ['0', '1', '1', '1'], 17: ['1', '0', '0', '0'], 18: ['1', '1', '1', '1'], 19: ['0', '1', '1', '1'], 20: ['1', '0', '0', '0'], 21: ['1', '0', '0', '0'], 22: ['0', '1', '1', '1'], 23: ['0', '1', '1', '1'], 24: ['1', '0', '0', '0'], 25: ['1', '1', '1', '1'], 26: ['0', '1', '1', '1'], 27: ['1', '0', '0', '0'], 28: ['1', '1', '1', '1'], 29: ['0', '0', '0', '0'], 30: ['1', '1', '1', '1'], 31: ['0', '1', '1', '1'], 32: ['1', '1', '1', '1'], 33: ['1', '0', '0', '0'], 34: ['1', '1', '1', '1'], 35: ['0', '0', '0', '0'], 36: ['1', '1', '1', '1'], 37: ['0', '0', '0', '0'], 38: ['1', '0', '0', '

[True]

In [71]:
def average_sequence(group):
    test = {}
    correct_sequence = ""
    for g in group:
        for i, c in enumerate(format(g, "0304b")):
            if i in test: 
                test[i].append(c)
            else:
                test[i] = [c]
    for i in range(len(test)):
        if len(test[i]) > 2:
            correct_sequence += mode(test[i])[0][0]
    return correct_sequence

In [8]:
def find_best_match(group):
    current = 200
    best_sequence = ""    
    for i in group:
        distance = []
        for j in group:
            distance.append(HammingDistance(i,j))        
        if np.average(distance) < current:
            best_sequence = i
            print(distance,np.average(distance),current, best_sequence)
            current = np.average(distance
    return best_sequence


SyntaxError: invalid syntax (<ipython-input-8-7ed7730bf81c>, line 12)

In [9]:
def CollapseGroupedSmart(grouped, ungrouped):
    collapsed = []
    for i in grouped:
        group = [i] * grouped[i]
        for j in ungrouped:
            if HammingDistance(i,j) < 4:
                group.append(j)
                ungrouped.remove(j)
        collapsed.append(group)
    return collapsed, ungrouped
def CollapseUngroupedSmart(ungrouped):
    collapsed = []
    for i in ungrouped:
        group = [i]
        ungrouped.remove(i)
        for j in ungrouped:
            if HammingDistance(i,j) < 4:
                group.append(j)
                ungrouped.remove(j)
        collapsed.append(group)
    return collapsed

In [10]:
%%time
grouped_grouped ,remaining  = CollapseGroupedSmart(groups,ungrouped)
ungrouped_grouped = CollapseUngroupedSmart(remaining)
for i in ungrouped_grouped:
    grouped_grouped.append(i)
final_grouping = ungrouped_grouped

Wall time: 34min 22s


In [72]:
for i in final_grouping:
    if len(i) > 0:
        for j in i:
            if len(format(j,"0304b")) > 304:
                print(i)

[...]


In [78]:
sequences = {}
for i in final_grouping:
    number_of_reads = len(i)
    if number_of_reads > 2:
        group_sequence = util.Binary2DNA(average_sequence(i))
        sequences[group_sequence] = number_of_reads
    elif number_of_reads == 2:
        sequences[util.Binary2DNA(format(i[0], "0304b"))] = 1
        sequences[util.Binary2DNA(format(i[1], "0304b"))] = 1
    else:
        group_sequence = util.Binary2DNA(format(i[0],"0304b"))
        sequences[group_sequence] = number_of_reads

In [108]:
n = 0
for i in dropletlist:
    if len(i) > 152:
        n+=1
print(n)
        


0


In [162]:
with open("collapsed.txt" , "w") as file:
    for w in sorted(collapsed, key=collapsed.get, reverse=True):
        file.write(util.Binary2DNA(format(w,"0304b")) + "\n")

...


...


...


...


...


...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




...


...


...


...


In [107]:
len(collapsed)

29319

In [82]:
len(sequences)

19130